In [16]:
import pandas as pd
from plot import plot
import numba
from statsmodels.tsa.arima.model import ARIMA
from pandas import DataFrame
from matplotlib import pyplot
from matplotlib.pyplot import figure
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np
from statsmodels.graphics.tsaplots import plot_acf
from statsmodels.graphics.tsaplots import plot_pacf
from sklearn.model_selection import train_test_split
import statsmodels.api as sm
from warnings import simplefilter
from statsmodels.tools.sm_exceptions import ConvergenceWarning
from statsmodels.tools.sm_exceptions import HessianInversionWarning
from statsmodels.tools.sm_exceptions import ValueWarning
from detecta import detect_cusum
import datetime
import pytz
import sklearn.metrics as skm
import copy
import pstats
import seaborn as sns
import os
import cProfile
import time
from multiprocessing import Pool

In [2]:
col_por_rel = [{'relevancia': 3, 'feature': 'ventovel2m'},
{'relevancia': 3, 'feature': 'ventovel10m'},
{'relevancia': 3, 'feature': 'ventodir10m'},
{'relevancia': 3, 'feature': 'umidrelmed2m'},
{'relevancia': 3, 'feature': 'umidrelmed1m'},
{'relevancia': 3, 'feature': 'tempminar2m'},
{'relevancia': 3, 'feature': 'tempminar1m'},
{'relevancia': 3, 'feature': 'tempmedar2m'},
{'relevancia': 3, 'feature': 'tempmedar1m'},
{'relevancia': 3, 'feature': 'tempmaxar2m'},
{'relevancia': 3, 'feature': 'tempmaxar1m'},
{'relevancia': 3, 'feature': 'radsolglb'},
{'relevancia': 3, 'feature': 'precacum'},
{'relevancia': 3, 'feature': 'prec'},
{'relevancia': 2, 'feature': 'umidsolonu20cm'},
{'relevancia': 2, 'feature': 'umidsolocm20cm'},
{'relevancia': 2, 'feature': 'tempsolonu5cm'},
{'relevancia': 2, 'feature': 'tempsolonu40cm'},
{'relevancia': 2, 'feature': 'tempsolonu2cm'},
{'relevancia': 2, 'feature': 'tempsolonu20cm'},
{'relevancia': 2, 'feature': 'tempsolonu10cm'},
{'relevancia': 2, 'feature': 'tempsolonu100cm'},
{'relevancia': 2, 'feature': 'tempsologra5cm'},
{'relevancia': 2, 'feature': 'tempsologra40cm'},
{'relevancia': 2, 'feature': 'tempsologra2cm'},
{'relevancia': 2, 'feature': 'tempsologra20cm'},
{'relevancia': 2, 'feature': 'tempsologra10cm'},
{'relevancia': 2, 'feature': 'tempsologra100cm'},
{'relevancia': 2, 'feature': 'tempsolocm5cm'},
{'relevancia': 2, 'feature': 'tempsolocm40cm'},
{'relevancia': 2, 'feature': 'tempsolocm2cm'},
{'relevancia': 2, 'feature': 'tempsolocm20cm'},
{'relevancia': 2, 'feature': 'tempsolocm10cm'},
{'relevancia': 2, 'feature': 'tempsolocm100cm'},
{'relevancia': 2, 'feature': 'tempminrelva'},
{'relevancia': 2, 'feature': 'tempmedrelva'},
{'relevancia': 2, 'feature': 'rajdir10m'},
{'relevancia': 2, 'feature': 'raj10m'},
{'relevancia': 2, 'feature': 'radparmed'},
{'relevancia': 1, 'feature': 'pressao'},
{'relevancia': 0, 'feature': 'molfoliar2m_sec'},
{'relevancia': 0, 'feature': 'molfoliar2m_mol'},
{'relevancia': 0, 'feature': 'molfoliar2m_con'},
{'relevancia': 0, 'feature': 'molfoliar1m_sec'},
{'relevancia': 0, 'feature': 'molfoliar1m_mol'},
{'relevancia': 0, 'feature': 'molfoliar1m_con'}]

In [3]:
def sep_anomalies(anomalies):
	anom_start = -1
	isolated_anomalies = []
	continuous_anomalies = []
	for i, anomaly in enumerate(anomalies):
		# Se o próximo for anomalia
		if i < (len(anomalies) - 1) and anomalies[i+1] == anomaly+1:
			# E o anterior não for ou for o primeiro da lista
			if anomalies[i-1] != anomaly-1 or i == 0:
				# É começo de uma contínua
				anom_start = anomaly
		# Se o anterior é anomalia e o próximo não for ou for o fim da lista, é fim de contínuo
		elif i > 0 and anomalies[i-1] == anomaly-1:
			continuous_anomalies.append((anom_start, anomaly))
			anom_start = -1
		# Se o próximo e o anterior não forem anomalia, é isolado
		else:
			isolated_anomalies.append(anomaly)
	return isolated_anomalies, continuous_anomalies

def seq_data(data, window_size=96):
	data_X = []
	data_Y = []
	for i in range(len(data) - (len(data) % window_size) - window_size):
		data_X.append(data[i:i+window_size])
		data_Y.append(data[i+window_size])
	return np.array(data_X), np.array(data_Y)

In [4]:
simplefilter("ignore", category=ConvergenceWarning)
simplefilter("ignore", category=HessianInversionWarning)
simplefilter("ignore", category=RuntimeWarning)
simplefilter("ignore", category=ValueWarning)

In [5]:
stations = pd.read_csv('../Dados/stations_list.csv',sep=';').stations.to_list()

In [6]:
# 1 dia
window_size = 96
# Multiplicador pra não deixar o desvio muito pequeno
# No cusum os limites recomendados são 4 desvios, com a folga de meio desvio dá mais ou menos isso
s = 3.2
min_std = 0
max_std = 15
# Valor inicial caso tenha anomalia desde o começo
std = min_std

In [7]:
stations = [23025122]
features = [
  'umidrelmed2m',
	'umidrelmed1m',
	'tempminar2m',
	'tempminar1m',
	'tempmedar2m',
	'tempmedar1m',
	'tempmaxar2m',
	'tempmaxar1m',
	'radsolglb',
	'precacum',
	'prec'
]

In [18]:
def timed_arima(i, x):
	try:
		pred = ARIMA(x, order=(1,0,0)).fit().forecast()[0]
	except Exception as e:
		pred = x[-1]
	if (i % 1000) == 0:
		print('Tempo de execução de 1000 itens', time.time() - t)
		t = time.time()
	return pred

In [19]:
def async_arima(x):
	try:
		pred = ARIMA(x, order=(1,0,0)).fit().forecast()[0]
	except Exception as e:
		pred = x[-1]
	return pred

In [25]:
def sort_np(arr):
	arr.sort(key=lambda ix: ix[0])
	arr = [ix[1] for ix in arr]
	return arr

def apply_arima(reshaped_data):
  predicted_series = list(map(async_arima, enumerate(reshaped_data)))
  return predicted_series

def calc_standart_devs(reshaped_data, max_std, min_std, s):
  return [max(min(np.std(x) * s, max_std), min_std) for x in reshaped_data]

In [27]:
with cProfile.Profile() as pr:
	for feature in features[:1]:
		for station in stations:
			df = pd.read_csv('../Dados/features/station_{}/export_automaticas_{}_{}.csv'.format(station, station, feature), sep=';')

			data = np.array(df[feature].to_list()[:30000])

			# Dados separado em janelas
			reshaped_data, targets = seq_data(data, window_size=window_size)
			processes = 6
			chunksize, extra = divmod(len(reshaped_data), processes * 4)
			if extra:
				chunksize += 1

			standart_d = calc_standart_devs(reshaped_data, max_std, min_std, s)
			t = time.perf_counter()

			predicted_series = apply_arima(reshaped_data)

			predicted_series = sort_np(predicted_series)

			anom_positions = [i for (i, prediction), std in zip(enumerate(predicted_series), standart_d) if abs(prediction - targets[i]) > std]

			series = data[window_size:]

			isolated, continuous = sep_anomalies(anom_positions)
	stats = pstats.Stats(pr)
	stats.sort_stats(pstats.SortKey.TIME)
	stats.dump_stats(filename='prof.prof')

c:\Users\Usuario\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\base\data.py:668: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  endog = np.asarray(endog)


In [14]:
for feature in features[:1]:
	for station in stations:
		df = pd.read_csv('../Dados/features/station_{}/export_automaticas_{}_{}.csv'.format(station, station, feature), sep=';')

		data = df[feature].to_list()[:5000]

		# Dados separado em janelas
		reshaped_data, targets = seq_data(data, window_size=window_size)
		processes = 6
		chunksize, extra = divmod(len(reshaped_data), processes * 4)
		if extra:
			chunksize += 1

		standart_d = [max(min(np.std(x) * s, max_std), min_std) for x in reshaped_data]
		t = time.perf_counter()
		print('abrindo threads')
		with Pool() as pool:
			predicted_series = list(pool.imap_unordered(async_arima, enumerate(reshaped_data), chunksize))
			predicted_series.sort(key=lambda ix: ix[0])
			predicted_series = [ix[1] for ix in predicted_series]
		# predicted_series = [timed_arima(x, i, t) for i, x in enumerate(reshaped_data)]
		print('fim', time.perf_counter() - t)
		anom_positions = [i for (i, prediction), std in zip(enumerate(predicted_series), standart_d) if abs(prediction - targets[i]) > std]

		series = data[window_size:]

		isolated, continuous = sep_anomalies(anom_positions)

		try:
			path = os.path.join('./results/data/{}'.format(feature))
			os.makedirs(path)
		except Exception as e:
			pass
		
		try:
			path = os.path.join('./results/images/{}'.format(feature))
			os.makedirs(path)
		except Exception as e:
			pass

		plot(series, detected_anomalies=isolated, continuous_anomalies=continuous, sec_plots=[predicted_series], std_dev=standart_d, save=True, img_name='./results/images/{}/{}_{}_result.jpg'.format(feature, station, feature), show=False)
	
		result = pd.DataFrame({
			'real_value': [data[i + window_size] for i in range(len(predicted_series))],
			'predictions': predicted_series,
			'anomaly': [1 if i in anom_positions else 0 for i in range(len(predicted_series))],
			'std': standart_d,
		})
		result.to_csv('./results/data/{}/{}_{}_result.csv'.format(feature, station, feature), sep=';',index=False)


In [ ]:
predicted_series = [ARIMA(x, order=(1,0,0)).fit().forecast()[0] for x in reshaped_data]

In [ ]:
plot(series, detected_anomalies=isolated, continuous_anomalies=continuous, sec_plots=[predicted_series], std_dev=standart_d)

In [ ]:
data = df[feature].to_list()
plot(data)